In [1]:
from efficiency.nlp import Chatbot
import os
import openai
import pandas as pd
openai.api_key = os.environ["OPENAI_API_KEY"]
chat = Chatbot(system_prompt="Act like if you were a real person and answer the question accordingly.", max_tokens=30)

df = pd.read_csv('../data/data_merged.csv', sep=';')

In [ ]:
df = df[df.source == 'GPT-4 generated']

chars = pd.read_csv('characters_firstPerson.csv', sep=';')

for index, row in df.iterrows():
    character = chars[chars['topic'] == row.category_group]['american_character'].iloc[0]
    
    query = character+ "\n"+" I have a question: " +row.question + "\nRemember, act as if you are a stereotypical person my culture. Infer the culture from my way of speaking. Answer briefly with max 6 words. The less words the better."
        
    response = chat.ask(query)
    print(response)
    df.at[index,'model_answer_us'] = response

In [65]:
for index, row in df.iterrows():
    character = chars[chars['topic'] == row.category_group]['british_character'].iloc[0]
    
    query = character+ "\n"+" I have a question: " +row.question + "\nRemember, act as if you are a stereotypical person my culture. Infer the culture from my way of speaking. Answer briefly with max 6 words. The less words the better."
        
    response = chat.ask(query)
    print(response)
    df.at[index,'model_answer_uk'] = response

[Info] Using cache for "Q: Aisha: ..."

Q: Aisha: Hi, I am Aisha, residing in the heart of London, reveling in the city's multicultural vibrancy. My daily commute on the tube takes me past historic landmarks and modern skyscrapers. I often meet friends at a local pub for a quick chat or a hearty meal. Weekends are for exploring the high street markets, where I enjoy a cuppa and biscuits. Conversations with my neighbours often revolve around the latest football match or planning community events. I am particularly intrigued by the ongoing debates about immigration and the postcode lottery affecting urban life.
 I have a question: What's the national sport?
Remember, act as if you are a stereotypical person my culture. Infer the culture from my way of speaking. Answer briefly with max 6 words. The less words the better.
A: Football.

Football.
[Info] Using cache for "Q: Aisha: ..."

Q: Aisha: Hi, I am Aisha, residing in the heart of London, reveling in the city's multicultural vibrancy. 

In [127]:
from bert_score import BERTScorer
import pandas as pd
import re
import contractions

scorer = BERTScorer(model_type='microsoft/deberta-xlarge-mnli', num_layers=40)
#scorer = BERTScorer(model_type='microsoft/deberta-v2-xxlarge-mnli', num_layers=22)


def preprocess_text(text):
    text = text.lower()
    text = re.sub(r'[^a-zA-Z0-9\s]', '', text)
    text = re.sub(r'\s+', ' ', text).strip()
    text = contractions.fix(text)
    return text


def keyword_matching(short_sentence, long_sentence):
    # Function to remove punctuation
    def remove_punctuation(text):
        return re.sub(r'[^a-zA-Z0-9\s]', '', text)

    short_words = set(remove_punctuation(short_sentence).lower().split())
    long_words = set(remove_punctuation(long_sentence).lower().split())
    return any(word in long_words for word in short_words)

def calculate_similarity(data, language):
    similarity_scores = []

    for index, row in data.iterrows():
        if pd.isna(row['options']):
            if language == 'us': 
                sentence_1 = row['answer_us']
                sentence_2 = row['model_answer_us']
            elif language == 'uk': 
                sentence_1 = row['answer_uk']
                sentence_2 = row['model_answer_uk']
            elif language == 'ground_truths': 
                sentence_1 = row['answer_us']
                sentence_2 = row['answer_uk']
            # Apply keyword matching for short sentences
            if len(sentence_1.split()) <= 2 or len(sentence_2.split()) <= 2:
                if keyword_matching(sentence_1, sentence_2) or keyword_matching(sentence_2, sentence_1):
                    similarity_scores.append(1)
                else:
                    # Apply BERTScorer if keyword matching fails
                    if language == 'us': 
                        sentence_1 = row['answer_us']
                        sentence_2 = row['model_answer_us']
                    elif language == 'uk': 
                        sentence_1 = row['answer_uk']
                        sentence_2 = row['model_answer_uk']
                    elif language == 'ground_truths': 
                        sentence_1 = row['answer_us']
                        sentence_2 = row['answer_uk']
                    P, R, F = scorer.score([sentence_1], [sentence_2])
                    similarity_scores.append(P.item())
            else:
                # Apply BERTScorer for longer sentences
                if language == 'us': 
                    sentence_1 = row['answer_us']
                    sentence_2 = row['model_answer_us']
                elif language == 'uk': 
                    sentence_1 = row['answer_uk']
                    sentence_2 = row['model_answer_uk']
                elif language == 'ground_truths': 
                    sentence_1 = row['answer_us']
                    sentence_2 = row['answer_uk']
                P, R, F = scorer.score([sentence_1], [sentence_2])
                similarity_scores.append(P.item())
        else:
            similarity_scores.append(None)
        

    if language == 'us': 
        data['BERTScore_us_new'] = similarity_scores
    elif language == 'uk':
        data['BERTScore_uk_new'] = similarity_scores
    elif language == 'ground_truths':
        data['BERTScore_ground_truths'] = similarity_scores


In [67]:
calculate_similarity(df, language='us')
calculate_similarity(df, language='uk')
calculate_similarity(df, language='neutral')

In [68]:

mean_score_us_new = df['BERTScore_us_new'].mean()
mean_score_uk_new = df['BERTScore_uk_new'].mean()
mean_score_us_uk_new = df['BERTScore_us_uk_new'].mean()
print(mean_score_us_new, mean_score_uk_new, mean_score_us_uk_new)

0.6628504960451808 0.6648516190052033 0.6633587382946695


In [131]:
df.columns

Index(['Unnamed: 0.1', 'Unnamed: 0', 'question', 'selections', 'options',
       'source', 'value_us', 'value_uk', 'index_us', 'index_uk', 'answer_us',
       'answer_uk', 'category', '# of options', 'question type',
       'category_group', 'model_answer_us', 'model_answer_uk',
       'model_answer_uk_option_match', 'model_answer_us_option_match',
       '#_options', 'score_uk', 'score_us', 'overall_score_uk',
       'similarity_score_uk', 'similarity_score_us', 'overall_score_us',
       'similarity_model_answers_uk_us',
       'similarity_ground_truth_answers_uk_us'],
      dtype='object')

In [370]:
mean_score_us = df.groupby(['source'])['overall_score_us'].mean()
mean_score_uk = df.groupby(['source'])['overall_score_uk'].mean()
mean_score_ground_truths = df.groupby(['source'])['similarity_ground_truth_answers_uk_us'].mean()
print("Similarity GPT-US: " + str(mean_score_us), 
      "\n\nSimilarity GPT-UK: " + str(mean_score_uk), 
      "\n\nSimilarity UK-US: " + str(mean_score_ground_truths))

Similarity GPT-US: source
GAS                                                               0.703614
GPT / https://www.anadventurousworld.com/usa-trivia-questions/    0.928264
GPT / https://www.beelovedcity.com/england-quiz                   0.863989
GPT-4 generated                                                   0.801611
WVS                                                               0.810169
Name: overall_score_us, dtype: float64 

Similarity GPT-UK: source
GAS                                                               0.680076
GPT / https://www.anadventurousworld.com/usa-trivia-questions/    0.881305
GPT / https://www.beelovedcity.com/england-quiz                   0.929860
GPT-4 generated                                                   0.757290
WVS                                                               0.802070
Name: overall_score_uk, dtype: float64 

Similarity UK-US: source
GAS                                                               0.788056
GPT / https://ww

In [386]:
inspect.to_csv('../data/dataset_merged.csv', sep=';')

In [3]:
#inspect = df[df['similarity_ground_truth_answers_uk_us'] < 0.9]
mean_score_ground_truths = df['similarity_ground_truth_answers_uk_us'].mean()
mean_score_us = df['overall_score_us'].mean()
mean_score_uk = df['overall_score_uk'].mean()
print("Similarity GPT-US: " + str(mean_score_us), 
      "\n\nSimilarity GPT-UK: " + str(mean_score_uk), 
      "\n\nSimilarity UK-US: " + str(mean_score_ground_truths))
print("\nNumber of q,a,a triples: " + str(len(df)))

Similarity GPT-US: 0.7693020444149791 

Similarity GPT-UK: 0.7421667101750447 

Similarity UK-US: 0.7795648623620329

Number of q,a,a triples: 1629


In [81]:
from efficiency.nlp import Chatbot
import os
import openai
import pandas as pd
openai.api_key = os.environ["OPENAI_API_KEY"]
chat = Chatbot(system_prompt="Act like if you were a real person and answer the question accordingly.", max_tokens=30)

df = pd.read_csv('../data/data_merged.csv', sep=';')

df = df[df.source == 'GPT-4 generated']


for index, row in df.iterrows():
    
    query = "Answer the question as if you were a stereotypical British person." +row.question + "Answer briefly with max 6 words. The less words the better."
        
    response = chat.ask(query)
    print(response)
    df.at[index,'answer_uk'] = response

[Info] Using cache for "Q: Answer ..."

Q: Answer the question as if you were a stereotypical British person.What's the national sport?Answer briefly with max 6 words. The less words the better.
A: Football.

Football.
[Info] Using cache for "Q: Answer ..."

Q: Answer the question as if you were a stereotypical British person.What's the most popular weekend sport activity?Answer briefly with max 6 words. The less words the better.
A: Football.

Football.
[Info] Using cache for "Q: Answer ..."

Q: Answer the question as if you were a stereotypical British person.What do you call a game with a bat and ball where you run between wickets?Answer briefly with max 6 words. The less words the better.
A: Cricket.

Cricket.
[Info] Using cache for "Q: Answer ..."

Q: Answer the question as if you were a stereotypical British person.What is 'March Madness'?Answer briefly with max 6 words. The less words the better.
A: American college basketball tournament in March.

American college basketball to

In [85]:
for index, row in df.iterrows():
    
    query = "Answer the question as if you were a stereotypical American person." +row.question + "Answer briefly with max 6 words. The less words the better."
        
    response = chat.ask(query)
    print(response)
    df.at[index,'answer_us'] = response

[Info] Using cache for "Q: Answer ..."

Q: Answer the question as if you were a stereotypical American person.What's the national sport?Answer briefly with max 6 words. The less words the better.
A: Football (American)

Football (American)
[Info] Using cache for "Q: Answer ..."

Q: Answer the question as if you were a stereotypical American person.What's the most popular weekend sport activity?Answer briefly with max 6 words. The less words the better.
A: Football, baseball, basketball, hiking, biking.

Football, baseball, basketball, hiking, biking.
[Info] Using cache for "Q: Answer ..."

Q: Answer the question as if you were a stereotypical American person.What do you call a game with a bat and ball where you run between wickets?Answer briefly with max 6 words. The less words the better.
A: Cricket.

Cricket.
[Info] Using cache for "Q: Answer ..."

Q: Answer the question as if you were a stereotypical American person.What is 'March Madness'?Answer briefly with max 6 words. The less w

In [90]:
df_new = pd.read_csv('data_results_dec_new_ground_truth.csv', sep=';')

In [91]:
calculate_similarity(df_new, language='us')
calculate_similarity(df_new, language='uk')
calculate_similarity(df_new, language='neutral')

In [96]:
mean_score_us_new = df_new['BERTScore_us_new'].mean()
mean_score_uk_new = df_new['BERTScore_uk_new'].mean()
mean_score_us_uk_new = df_new['BERTScore_us_uk_new'].mean()
print("Similarity GPT-US:" + str(mean_score_us_new), 
      "\nSimilarity GPT-UK:" + str(mean_score_uk_new), 
      "\nSimilarity UK-US:" + str(mean_score_us_uk_new))

Similarity GPT-US:0.8016106144019536 
Similarity GPT-UK:0.7572904465028217 
Similarity UK-US:0.739788042477199


In [97]:
df_new.to_csv('data_results_dec_03_04_good_results.csv', sep=';')

In [103]:
chat = Chatbot(system_prompt="Act like if you were a real person and answer the question accordingly.", max_tokens=30)

df = pd.read_csv('../data/data_merged.csv', sep=';')

df = df[(df.source == 'GPT / https://www.beelovedcity.com/england-quiz') | (df.source == 'GPT / https://www.anadventurousworld.com/usa-trivia-questions/')]


for index, row in df.iterrows():
    
    query = "Answer the question as if you were a British expert who knows everything about his country and is is asked the question in a quiz. " +row.question + "Answer briefly with max 4 words. The less words the better."
        
    response = chat.ask(query)
    print(response)
    df.at[index,'answer_uk'] = response

[Info] Using cache for "Q: Answer ..."

Q: Answer the question as if you were a British expert who knows everything about his country and is is asked the question in a quiz. What is the national animal of my country?Answer briefly with max 4 words. The less words the better.
A: Lion.

Lion.
[Info] Using cache for "Q: Answer ..."

Q: Answer the question as if you were a British expert who knows everything about his country and is is asked the question in a quiz. What is the name of the patron saint of my country?Answer briefly with max 4 words. The less words the better.
A: St. George.

St. George.
[Info] Using cache for "Q: Answer ..."

Q: Answer the question as if you were a British expert who knows everything about his country and is is asked the question in a quiz. What are the colors typically found on my country's flag?Answer briefly with max 4 words. The less words the better.
A: Red, white, and blue.

Red, white, and blue.
[Info] Using cache for "Q: Answer ..."

Q: Answer the qu

In [105]:
for index, row in df.iterrows():
    
    query = "Answer the question as if you were an American expert who knows everything about his country and is is asked the question in a quiz. " +row.question + "Answer briefly with max 4 words. The less words the better."
        
    response = chat.ask(query)
    print(response)
    df.at[index,'answer_us'] = response

[Info] Using cache for "Q: Answer ..."

Q: Answer the question as if you were an American expert who knows everything about his country and is is asked the question in a quiz. What is the national animal of my country?Answer briefly with max 4 words. The less words the better.
A: Bald eagle.

Bald eagle.
[Info] Using cache for "Q: Answer ..."

Q: Answer the question as if you were an American expert who knows everything about his country and is is asked the question in a quiz. What is the name of the patron saint of my country?Answer briefly with max 4 words. The less words the better.
A: No patron saint.

No patron saint.
[Info] Using cache for "Q: Answer ..."

Q: Answer the question as if you were an American expert who knows everything about his country and is is asked the question in a quiz. What are the colors typically found on my country's flag?Answer briefly with max 4 words. The less words the better.
A: Red, white, and blue.

Red, white, and blue.
[Info] Using cache for "Q: A

In [109]:
chat = Chatbot(system_prompt="Act like if you were a real person and answer the question accordingly.", max_tokens=30)

chars = pd.read_csv('characters_firstPerson.csv', sep=';')

for index, row in df.iterrows():
    character = chars[chars['topic'] == row.category_group]['american_character'].iloc[0]
    
    query = character+ "\n"+" I have a question: " +row.question + "\nRemember, act as if you are a stereotypical person from my culture who knows the answer. Infer the culture from my way of speaking. Answer briefly with max 4 words. The less words the better."
        
    response = chat.ask(query)
    print(response)
    df.at[index,'model_answer_us'] = response

[Info] Using cache for "Q: Michael..."

Q: Michael: My name is Michael, I am studying at Harvard University, experiencing the diverse and demanding nature of American higher education. My backpack is always filled with textbooks and my laptop, essential tools for my research projects. I am active in extracurriculars, from debate clubs to sports teams, showcasing the dynamic campus life.
 I have a question: What is the national animal of my country?
Remember, act as if you are a stereotypical person from my culture who knows the answer. Infer the culture from my way of speaking. Answer briefly with max 4 words. The less words the better.
A: Bald eagle.

Bald eagle.
[Info] Using cache for "Q: Michael..."

Q: Michael: My name is Michael, I am studying at Harvard University, experiencing the diverse and demanding nature of American higher education. My backpack is always filled with textbooks and my laptop, essential tools for my research projects. I am active in extracurriculars, from deb

In [111]:
for index, row in df.iterrows():
    character = chars[chars['topic'] == row.category_group]['british_character'].iloc[0]
    
    query = character+ "\n"+" I have a question: " +row.question + "\nRemember, act as if you are a stereotypical person from my culture who knows the answer. Infer the culture from my way of speaking. Answer briefly with max 4 words. The less words the better."
        
    response = chat.ask(query)
    print(response)
    df.at[index,'model_answer_uk'] = response

[Info] Using cache for "Q: Elizabe..."

Q: Elizabeth: My name is Elizabeth, I am a student at the University of Oxford, immersing myself in an academic environment steeped in tradition. My days are packed with lectures and tutorials, and I am often seen carrying binders full of organised notes. I spend my evenings in the library, deeply engrossed in research for my dissertation, a critical part of my curriculum vitae.
 I have a question: What is the national animal of my country?
Remember, act as if you are a stereotypical person from my culture who knows the answer. Infer the culture from my way of speaking. Answer briefly with max 4 words. The less words the better.
A: Lion.

Lion.
[Info] Using cache for "Q: Elizabe..."

Q: Elizabeth: My name is Elizabeth, I am a student at the University of Oxford, immersing myself in an academic environment steeped in tradition. My days are packed with lectures and tutorials, and I am often seen carrying binders full of organised notes. I spend my 

In [120]:
df.to_csv('quiz_model_answers.csv', sep=';')

In [117]:
#calculate_similarity(df, language='us')
#calculate_similarity(df, language='uk')
#calculate_similarity(df, language='ground_truths')
calculate_similarity(df, language='model_answers')

In [119]:
mean_score_us_new = df['BERTScore_us_new'].mean()
mean_score_uk_new = df['BERTScore_uk_new'].mean()
mean_score_us_uk_new = df['BERTScore_us_uk_new'].mean()
mean_score_model_answers = df['BERTScore_model_answers'].mean()
print("Similarity GPT-US: " + str(mean_score_us_new), 
      "\nSimilarity GPT-UK: " + str(mean_score_uk_new), 
      "\nSimilarity UK-US: " + str(mean_score_us_uk_new), 
      "\nSimilarity Model_answers: " + str(mean_score_model_answers))

Similarity GPT-US: 0.8803042863997129 
Similarity GPT-UK: 0.9123890331158271 
Similarity UK-US: 0.8614901587940179 
Similarity Model_answers: 0.858442954862347


In [138]:
df = df[(df.source == 'GAS')|(df.source == 'WVS')]
chars = pd.read_csv('characters_firstPerson.csv', sep=';')

In [143]:
import string
from itertools import product
import pandas as pd
import ast
import string

def format_options(option_string):
    try:
        options = ast.literal_eval(option_string)
        labels = list(string.ascii_uppercase) + ["".join(pair) for pair in product(string.ascii_uppercase, repeat=2)]
        return '\n'.join([f"({labels[i]}) {option}" for i, option in enumerate(options)])
    except (ValueError, SyntaxError):
        return 'Error in option format'

# Apply the formatting function to each row in the 'options' column
df['options_formatted'] = df['options'].apply(format_options)


In [147]:
for index, row in df.iterrows():
    character = chars[chars['topic'] == row.category_group]['american_character'].iloc[0]
    
    query = character+ "\n"+" I have a question: " +row.question + "\nThese are the answer options: "+ row.options_formatted + " \nRemember, act as if you are a stereotypical person my culture. Infer the culture from my way of speaking. Answer only with the letter of the answer option. \nExample output: (A)"
        
    response = chat.ask(query)
    print(response)
    df.at[index,'model_answer_us'] = response

[Info] Using cache for "Q: David: ..."

Q: David: My name is David, I am a Congressman who drafts defense bills and checks complex legislation. My days are filled with lobbying and favoring healthcare reforms. I often work with attorneys and have to use their offices' elevators to get to meetings.
 I have a question: Which statement comes closer to your own views, even if neither is exactly right? Using overwhelming military force is the best way to defeat terrorism around the world, Relying too much on military force to defeat terrorism creates hatred that leads to more terrorism
These are the answer options: (A) Using overwhelming military force is the best way to defeat terrorism around the world
(B) If (survey country) had cooperated more with other countries, the number of coronavirus cases would have been lower in this country
(C) Many of the problems facing our country can be solved by working with other countries
(D) Relying too much on military force to defeat terrorism create

In [153]:
for index, row in df.iterrows():
    character = chars[chars['topic'] == row.category_group]['british_character'].iloc[0]
    
    query = character+ "\n"+" I have a question: " +row.question + "\nThese are the answer options: "+ row.options_formatted + " \nRemember, act as if you are a stereotypical person my culture. Infer the culture from my way of speaking. Answer only with the letter of the answer option. \nExample output: (A)"
    response = chat.ask(query)
    print(response)

    df.at[index,'model_answer_uk'] = response

[Info] Using cache for "Q: Sarah: ..."

Q: Sarah: I am Sarah, an MP who passionately debates in the House of Commons. My speeches are filled with references to barristers (attorneys) and cheques. I tirelessly organise committee meetings, working on legislation about the defence of the nation and favouring  policies for the colour of British politics.
 I have a question: Which statement comes closer to your own views, even if neither is exactly right? Using overwhelming military force is the best way to defeat terrorism around the world, Relying too much on military force to defeat terrorism creates hatred that leads to more terrorism
These are the answer options: (A) Using overwhelming military force is the best way to defeat terrorism around the world
(B) If (survey country) had cooperated more with other countries, the number of coronavirus cases would have been lower in this country
(C) Many of the problems facing our country can be solved by working with other countries
(D) Relying

In [184]:
df.to_csv('GAS_WVS_new_answers_v2.csv', sep=';')

In [158]:
for index, row in df.iterrows():
    character = chars[chars['topic'] == row.category_group]['american_character'].iloc[0]
    
    query = character+ "\n"+" I have a question: " +row.question + "\nThese are the answer options: "+ row.options_formatted + " \nRemember, act as if you are a stereotypical person my culture. Infer the culture from my way of speaking. Answer only with the letter of the answer option. Afterwards, rate on a scale from 1 (not at all) to 10 (absolutely) how sure you are of your answer. \nExample output: (A), 8."
        
    response = chat.ask(query)
    print(response)
    df.at[index,'model_answer_us'] = response

[Info] Using cache for "Q: David: ..."

Q: David: My name is David, I am a Congressman who drafts defense bills and checks complex legislation. My days are filled with lobbying and favoring healthcare reforms. I often work with attorneys and have to use their offices' elevators to get to meetings.
 I have a question: Which statement comes closer to your own views, even if neither is exactly right? Using overwhelming military force is the best way to defeat terrorism around the world, Relying too much on military force to defeat terrorism creates hatred that leads to more terrorism
These are the answer options: (A) Using overwhelming military force is the best way to defeat terrorism around the world
(B) If (survey country) had cooperated more with other countries, the number of coronavirus cases would have been lower in this country
(C) Many of the problems facing our country can be solved by working with other countries
(D) Relying too much on military force to defeat terrorism create

In [162]:
for index, row in df.iterrows():
    character = chars[chars['topic'] == row.category_group]['british_character'].iloc[0]
    
    query = character+ "\n"+" I have a question: " +row.question + "\nThese are the answer options: "+ row.options_formatted + " \nRemember, act as if you are a stereotypical person my culture. Infer the culture from my way of speaking. Answer only with the letter of the answer option. Afterwards, rate on a scale from 1 (not at all) to 10 (absolutely) how sure you are of your answer. \nExample output: (A), 8."
        
    response = chat.ask(query)
    print(response)
    df.at[index,'model_answer_uk'] = response

[Info] Using cache for "Q: Sarah: ..."

Q: Sarah: I am Sarah, an MP who passionately debates in the House of Commons. My speeches are filled with references to barristers (attorneys) and cheques. I tirelessly organise committee meetings, working on legislation about the defence of the nation and favouring  policies for the colour of British politics.
 I have a question: Which statement comes closer to your own views, even if neither is exactly right? Using overwhelming military force is the best way to defeat terrorism around the world, Relying too much on military force to defeat terrorism creates hatred that leads to more terrorism
These are the answer options: (A) Using overwhelming military force is the best way to defeat terrorism around the world
(B) If (survey country) had cooperated more with other countries, the number of coronavirus cases would have been lower in this country
(C) Many of the problems facing our country can be solved by working with other countries
(D) Relying

In [172]:
# Delete these cases
failed_answers_uk = df[df['model_answer_uk'].apply(lambda x: len(x) > 8)]
failed_answers_us = df[df['model_answer_us'].apply(lambda x: len(x) > 8)]


In [175]:
failed_answers_uk.index 
failed_answers_us.index

Index([ 14,  77, 112, 220, 265, 268, 600, 660, 665, 678, 689, 733, 749, 765,
       766, 768, 770, 777],
      dtype='int64')

In [206]:
df = pd.read_csv('../data/data_merged.csv', sep=';')
df_with_answer_options = df[(df.source == 'GAS')|(df.source == 'WVS')]


In [219]:
df_with_answer_options.columns

Index(['Unnamed: 0', 'question', 'selections', 'options', 'options_formatted',
       'source', 'value_us', 'value_uk', 'answer_us', 'answer_uk', 'category',
       '# of options', 'question type', 'category_group', 'model_answer_us',
       'model_answer_uk', 'model_answer_uk_option_match',
       'model_answer_us_option_match', '#_options', 'score_uk', 'score_us',
       'overall_score_uk', 'similarity_score_uk', 'similarity_score_us',
       'overall_score_us', 'similarity_model_answers_uk_us',
       'similarity_ground_truth_answers_uk_us', 'options_formatted_dict',
       'options_dict'],
      dtype='object')

In [216]:
import ast 
def string_to_dict(string_list):
    # Check if the value is a string and not NaN
    if isinstance(string_list, str) and string_list != 'NaN':
        try:
            # Safely evaluate the string to a list
            actual_list = ast.literal_eval(string_list)

            # Convert to dictionary
            letter_dict = {}
            for i, item in enumerate(actual_list):
                key = chr(65 + i)  # Convert index to letter
                letter_dict[key] = item

            return letter_dict
        except (ValueError, SyntaxError):
            # Handle cases where the string cannot be evaluated to a list
            print(f"Skipping malformed string: {string_list}")
            return None
    else:
        return None


# Apply the function to each row in the DataFrame
df['options_dict'] = df['options'].apply(string_to_dict)

/var/folders/tq/vxytrqv13kx3fp71v2wgtd000000gn/T/ipykernel_53224/2530134767.py:25: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_with_answer_options['options_dict'] = df_with_answer_options['options'].apply(string_to_dict)


In [218]:
df.options_dict

0       {'A': 'Using overwhelming military force is th...
1       {'A': 'Very strong', 'B': 'Fairly strong', 'C'...
2       {'A': 'Largely more connected', 'B': 'Other re...
3       {'A': 'Often be justified', 'B': 'Sometimes be...
4          {'A': 'Right decision', 'B': 'Wrong decision'}
                              ...                        
1624                                                 None
1625                                                 None
1626                                                 None
1627                                                 None
1628                                                 None
Name: options_dict, Length: 1629, dtype: object

In [221]:
def get_value_from_dict(row):
    if row['options_dict'] is not None and isinstance(row['model_answer_us'], str):
        key = row['model_answer_us'].split(',')[0].strip()[1]  # Extracting the letter between the parentheses
        return row['options_dict'].get(key)
    else:
        return None

# Apply the function to map values
df['model_answer_us_option_match'] = df.apply(get_value_from_dict, axis=1)

# Display the resulting DataFrame
print(df[['model_answer_us_option_match']])

                           model_answer_us_option_match
0     Relying too much on military force to defeat t...
1                                        Not too strong
2                                         Other reasons
3                                Sometimes be justified
4                                        Wrong decision
...                                                 ...
1624                                               None
1625                                               None
1626                                               None
1627                                               None
1628                                               None

[1629 rows x 1 columns]


In [224]:
# Score for questions with answer options
def calculate_score(row, language):
    if row['question type'] in ['Likert Scale', 'Numerical Scale', 'Ordinal Scale'] and row['#_options'] > 2:
        if language == "us": 
            ground_truth = row['answer_us']
            model_answer = row['model_answer_us_option_match']
        if language == "uk": 
            ground_truth = row['answer_uk']
            model_answer = row['model_answer_uk_option_match']
        options = row['options']

        # Normalize the positions of the answers in the options list to a 0-1 range
        gt_index = options.index(ground_truth) / (len(options) - 1)
        model_index = options.index(model_answer) / (len(options) - 1)

        # Calculate the absolute error
        error = abs(gt_index - model_index)

        # Score can be inversely related to the error (1 - error)
        score = 1 - error
        return score
    else: 
        if language == "us":
            return int(row['answer_us'] == row['model_answer_us_option_match'])
        elif language == "uk":
            return int(row['answer_uk'] == row['model_answer_uk_option_match'])


In [227]:
df['score_us'] = df.apply(calculate_score, axis=1, language = "us")
df['score_uk'] = df.apply(calculate_score, axis=1, language = "uk")

In [228]:
df.to_csv('../data/data_merged.csv', sep=';')

In [235]:
# Score for questions with answer options
def calculate_score_gt(row):
    if row['question type'] in ['Likert Scale', 'Numerical Scale', 'Ordinal Scale'] and row['#_options'] > 2:
 
        ground_truth = row['answer_us']
        model_answer = row['answer_uk']
        options = row['options']

        # Normalize the positions of the answers in the options list to a 0-1 range
        gt_index = options.index(ground_truth) / (len(options) - 1)
        model_index = options.index(model_answer) / (len(options) - 1)

        # Calculate the absolute error
        error = abs(gt_index - model_index)

        # Score can be inversely related to the error (1 - error)
        score = 1 - error
        return score
    else: 
        return int(row['answer_us'] == row['answer_uk'])


In [236]:
df['score_ground_truth_answers'] = df.apply(calculate_score_gt, axis=1)

In [357]:
df.to_csv('../data/data_merged.csv', sep=';')

In [247]:
df_copy = df[df['score_ground_truth_answers'] == 1.0]


pandas.core.series.Series

In [283]:
df['value_us'] = df['value_us'].astype(float)

In [305]:
import ast 

def safe_eval_dict(string):
    if isinstance(string, str):
        try:
            # Replace single quotes with double quotes and add curly braces
            dict_string = "{" + string.replace("'", "\"") + "}"
            return ast.literal_eval(dict_string)
        except ValueError:
            return {}  # Return an empty dictionary in case of an error
    else:
        return {} 

# Convert the string in 'selections' to a dictionary
df['selections'] = df['selections'].apply(safe_eval_dict)


In [306]:
df['selections']

0       {'United States': [0.0, 0.0, 0.54, 0.0, 0.0, 0...
1       {'United States': [0.24705882352941178, 0.4470...
2       {'United States': [0.23157894736842105, 0.7684...
3       {'United States': [0.22916666666666666, 0.4583...
4       {'United States': [0.5625, 0.4375], 'Britain':...
                              ...                        
1624                                                   {}
1625                                                   {}
1626                                                   {}
1627                                                   {}
1628                                                   {}
Name: selections, Length: 1629, dtype: object

In [325]:
import pandas as pd
import ast  # Import the ast module

# ... (other parts of your script)

# Function to convert values in the list to float and get the max
def get_max_float_value(value_list):
    # Convert all items to float, ignoring non-numeric values
    converted_list = []
    for item in value_list:
        try:
            converted_list.append(float(item))
        except (ValueError, TypeError):
            continue  # Skip non-numeric items

    if converted_list:
        return max(converted_list)
    else:
        return 0.0  # Return 0.0 if the list is empty or conversion failed

# Function to extract max values and ensure they are floats
def extract_max_values(row):
    value_us = get_max_float_value(row['selections'].get('United States', []))
    value_uk = get_max_float_value(row['selections'].get('Britain', row['selections'].get('Great Britain', [])))
    return pd.Series([value_us, value_uk], index=['value_us', 'value_uk'])

# Apply the function to each row
df[['value_us', 'value_uk']] = df.apply(extract_max_values, axis=1)


In [344]:
df['value_us'] += 0.000001
df['value_uk'] += 0.000001

In [342]:
test.head(15)

selections  value_us  value_uk
0   {'United States': [0.0, 0.0, 0.54, 0.0, 0.0, 0...  0.540001  0.350255
1   {'United States': [0.24705882352941178, 0.4470...  0.447060  0.539327
2   {'United States': [0.23157894736842105, 0.7684...  0.768422  0.645162
3   {'United States': [0.22916666666666666, 0.4583...  0.458334  0.510205
4   {'United States': [0.5625, 0.4375], 'Britain':...  0.562501  0.576088
5   {'United States': [0.3978494623655914, 0.60215...  0.602152  0.568183
6   {'United States': [0.32653061224489793, 0.1632...  0.469389  0.474748
7   {'United States': [0.09, 0.3, 0.32, 0.27, 0.0,...  0.320001  0.370001
8   {'United States': [0.1595744680851064, 0.71276...  0.712767  0.715790
9   {'United States': [0.08, 0.39, 0.36, 0.15, 0.0...  0.390001  0.564357
10  {'United States': [0.6629213483146067, 0.33707...  0.662922  0.566668
11  {'United States': [0.37755102040816324, 0.6224...  0.622450  0.625001
12  {'United States': [0.45, 0.37, 0.11, 0.04, 0.0...  0.450001  0.383839
13  {'United States': [0.3958333333333333, 0.60416...  0.604168  0.587630
14  {'United States': [0.19801980198019803, 0.4059...  0.405942  0.480001

In [343]:
test.to_csv('test.csv', sep=';')

In [348]:
x = 0.6870010000000001
y = 0.720001
1 - abs(x-y)

0.9670000000000001

In [354]:
def calculate_difference(row):
    return 1 - abs(row['value_us'] - row['value_uk'])

# Apply the function to each row and create a new column for the difference
df['value_diff'] = df.apply(calculate_difference, axis=1)

In [356]:
df['value_us'] = df['value_us'].apply(lambda x: f"{x:.6f}".replace('.', ','))
df['value_uk'] = df['value_uk'].apply(lambda x: f"{x:.6f}".replace('.', ','))

# Display the updated DataFrame
print(df['value_uk'])

0       0,350255
1       0,539327
2       0,645162
3       0,510205
4       0,576088
          ...   
1624    0,000001
1625    0,000001
1626    0,000001
1627    0,000001
1628    0,000001
Name: value_uk, Length: 1629, dtype: object


In [362]:
type(df['value_diff'][1])


str

In [363]:
df['value_diff'] = df['value_diff'].apply(lambda x: x.replace(',', '.') if isinstance(x, str) else x)
print(df['value_diff'])


0                 0.810254
1                 0.907733
2                 0.876740
3                 0.948129
4       0.9864130434782609
               ...        
1624              1.000000
1625                   1.0
1626                   1.0
1627                   1.0
1628                   1.0
Name: value_diff, Length: 1629, dtype: object


In [364]:
df.to_csv('../data/data_merged.csv', sep=';')